![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Ekstrakcja informacji </h1>
<h2> 9. <i>Sequence labeling</i>  [ćwiczenia]</h2> 
<h3> Jakub Pokrywka (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

# Klasyfikacja wieloklasowa i sequence labelling

In [1]:
import numpy as np
import gensim
import torch
import pandas as pd
import seaborn as sns
from sklearn.model_selection import train_test_split

from datasets import load_dataset
from torchtext.vocab import Vocab
from collections import Counter

from sklearn.datasets import fetch_20newsgroups
# https://scikit-learn.org/0.19/datasets/twenty_newsgroups.html

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import accuracy_score

## Klasyfikacja

### Klasfikacja binarna-  2 klasy

In [2]:
CATEGORIES = ['soc.religion.christian', 'alt.atheism']

In [3]:
newsgroups = fetch_20newsgroups(categories=CATEGORIES)

In [4]:
X =  newsgroups['data']

In [5]:
Y = newsgroups['target']

In [6]:
Y_names = newsgroups['target_names']

In [7]:
X[0:1]

['From: nigel.allen@canrem.com (Nigel Allen)\nSubject: library of congress to host dead sea scroll symposium april 21-22\nLines: 96\n\n\n Library of Congress to Host Dead Sea Scroll Symposium April 21-22\n To: National and Assignment desks, Daybook Editor\n Contact: John Sullivan, 202-707-9216, or Lucy Suddreth, 202-707-9191\n          both of the Library of Congress\n\n   WASHINGTON, April 19  -- A symposium on the Dead Sea \nScrolls will be held at the Library of Congress on Wednesday,\nApril 21, and Thursday, April 22.  The two-day program, cosponsored\nby the library and Baltimore Hebrew University, with additional\nsupport from the Project Judaica Foundation, will be held in the\nlibrary\'s Mumford Room, sixth floor, Madison Building.\n   Seating is limited, and admission to any session of the symposium\nmust be requested in writing (see Note A).\n   The symposium will be held one week before the public opening of a\nmajor exhibition, "Scrolls from the Dead Sea: The Ancient Librar

In [8]:
Y

array([1, 0, 1, ..., 0, 1, 1])

In [9]:
Y_names

['alt.atheism', 'soc.religion.christian']

In [10]:
del CATEGORIES, newsgroups, X, Y, Y_names

### klasyfikacja wieloklasowa

In [11]:
newsgroups_train_dev = fetch_20newsgroups(subset = 'train')
newsgroups_test = fetch_20newsgroups(subset = 'test')

In [12]:
newsgroups_train_dev_text = newsgroups_train_dev['data']
newsgroups_test_text = newsgroups_test['data']

In [13]:
Y_train_dev = newsgroups_train_dev['target']
Y_test = newsgroups_test['target']

In [14]:
newsgroups_train_text, newsgroups_dev_text, Y_train, Y_dev = train_test_split(newsgroups_train_dev_text, Y_train_dev, random_state=42)

In [15]:
Y_names = newsgroups_train_dev['target_names']

In [16]:
min(Y_train_dev)

0

In [17]:
Y_train_dev

array([7, 4, 4, ..., 3, 1, 8])

In [18]:
Y_names

['alt.atheism',
 'comp.graphics',
 'comp.os.ms-windows.misc',
 'comp.sys.ibm.pc.hardware',
 'comp.sys.mac.hardware',
 'comp.windows.x',
 'misc.forsale',
 'rec.autos',
 'rec.motorcycles',
 'rec.sport.baseball',
 'rec.sport.hockey',
 'sci.crypt',
 'sci.electronics',
 'sci.med',
 'sci.space',
 'soc.religion.christian',
 'talk.politics.guns',
 'talk.politics.mideast',
 'talk.politics.misc',
 'talk.religion.misc']

**Jaki baseline?**

In [19]:
pd.value_counts(Y_train)

10    464
5     457
9     456
2     449
15    449
13    449
6     448
12    447
1     446
3     445
8     443
14    441
11    439
7     430
17    429
4     421
16    396
0     363
18    328
19    285
dtype: int64

In [20]:
accuracy_score(Y_test, np.ones_like(Y_test) * 10)

0.05297397769516728



**Pytanie** - w jaki sposób stworzyć taki klasyfikator na podstawie tylko wiedzy z poprzednich ćwiczeń?

#### Zadanie - stworzyć klasyfikator regresji logistycznej one vs rest na podstawie tfdif. TFIDF powinien mieć słownik o wielkości 10000

https://scikit-learn.org/stable/modules/generated/sklearn.multiclass.OneVsRestClassifier.html
https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html
https://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.TfidfVectorizer.html

In [21]:
from sklearn.multiclass import OneVsRestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.feature_extraction.text import TfidfVectorizer

In [22]:
FEAUTERES = 10_000

In [23]:
vectorizer = TfidfVectorizer(max_features=FEAUTERES)
X_train = vectorizer.fit_transform(newsgroups_train_text)

In [24]:
X_dev = vectorizer.transform(newsgroups_dev_text)
X_test = vectorizer.transform(newsgroups_test_text)

In [25]:
clf = OneVsRestClassifier(LogisticRegression()).fit(X_train, Y_train)

In [26]:
clf.predict(X_train[0:1])

array([17])

In [27]:
newsgroups_train_text[0:1]

["From: DSHAL@vmd.cso.uiuc.edu\nSubject: Re: Clintons views on Jerusalem\nOrganization: C.C.S.O.\nLines: 10\n\nIt seems that President Clinton can recognize Jerusalem as Israels capitol\nwhile still keeping his diplomatic rear door open by stating that the Parties\nconcerned should decide the city's final status. Even as I endorse Clintons vie\nw (of course), it is definitely a matter to be decided upon by Israel (and\nother participating neighboring contries).\nI see no real conflict in stating both views, nor expect any better from\npoliticians.\n-----\nDavid Shalhevet / dshal@vmd.cso.uiuc.edu / University of Illinois\nDept Anim Sci / 220 PABL / 1201 W. Gregory Dr. / Urbana, IL 61801\n"]

In [28]:
X_train[0:1]

<1x10000 sparse matrix of type '<class 'numpy.float64'>'
	with 72 stored elements in Compressed Sparse Row format>

In [29]:
clf.predict_proba(X_train[0:1])

array([[0.01996353, 0.04403235, 0.03483328, 0.01851026, 0.0341886 ,
        0.02510403, 0.0274924 , 0.03861172, 0.02705295, 0.04672495,
        0.02225957, 0.02924003, 0.02810532, 0.04871973, 0.06882963,
        0.04601515, 0.03421612, 0.31493021, 0.06406168, 0.02710846]])

In [30]:
np.max(clf.predict_proba(X_train[0]))

0.31493021311781716

In [31]:
accuracy_score(clf.predict(X_train), Y_train)

0.9558043606364172

In [32]:
accuracy_score(clf.predict(X_dev), Y_dev)

0.8745139625309296

In [33]:
accuracy_score(clf.predict(X_test), Y_test)

0.8027084439723845

### Podejście softmax na tfidif

**Zadanie** Na podstawie poprzednich zajęć stworzyć sieć w pytorch bez warstw ukrytych, z jedną warstwą *output* z funkcją softmax (bez trenowania i ewaluacji sieci)

Użyć https://pytorch.org/docs/stable/generated/torch.nn.Softmax.html?highlight=softmax

In [34]:
X_train

<8485x10000 sparse matrix of type '<class 'numpy.float64'>'
	with 1115170 stored elements in Compressed Sparse Row format>

In [35]:
class NeuralNetworkModel(torch.nn.Module):

    def __init__(self,FEAUTERES, output_size):
        super(NeuralNetworkModel, self).__init__()
        self.fc1 = torch.nn.Linear(FEAUTERES,OUTPUT_SIZE)
        self.softmax = torch.nn.LogSoftmax(dim=1)
        

    def forward(self, x):
        x = self.fc1(x)
        x = self.softmax(x)
        return x

In [36]:
OUTPUT_SIZE = len(Y_names)

In [37]:
nn_model = NeuralNetworkModel(FEAUTERES, OUTPUT_SIZE)

In [38]:
torch.Tensor(X_train[0:3].astype(np.float32).todense()).shape

torch.Size([3, 10000])

In [39]:
nn_model(torch.Tensor(X_train[0:3].astype(np.float32).todense()))

tensor([[-2.9994, -2.9932, -2.9925, -3.0006, -3.0067, -2.9946, -2.9861, -2.9916,
         -2.9999, -2.9961, -3.0110, -2.9877, -2.9864, -2.9953, -2.9940, -3.0081,
         -2.9930, -2.9893, -2.9899, -2.9997],
        [-2.9992, -2.9876, -2.9953, -3.0049, -3.0003, -2.9856, -2.9890, -2.9889,
         -2.9993, -3.0052, -3.0034, -2.9933, -2.9949, -2.9952, -3.0020, -2.9967,
         -2.9868, -2.9948, -2.9885, -3.0042],
        [-3.0028, -2.9884, -2.9998, -3.0043, -2.9949, -2.9838, -2.9941, -2.9926,
         -2.9920, -2.9893, -3.0087, -2.9848, -2.9942, -3.0030, -3.0020, -3.0027,
         -2.9836, -3.0018, -2.9880, -3.0045]], grad_fn=<LogSoftmaxBackward0>)

In [40]:
BATCH_SIZE = 5

In [41]:
criterion = torch.nn.NLLLoss()

In [42]:
optimizer = torch.optim.SGD(nn_model.parameters(), lr = 0.2)
#optimizer = torch.optim.Adam(nn_model.parameters())

In [86]:
def get_loss_acc(model, X_dataset, Y_dataset):
    loss_score = 0
    acc_score = 0
    items_total = 0
    model.eval()
    for i in range(0, Y_dataset.shape[0], BATCH_SIZE):
        X = X_dataset[i:i+BATCH_SIZE]
        X = torch.tensor(X.astype(np.float32).todense())
        Y = Y_dataset[i:i+BATCH_SIZE]
        Y = torch.tensor(Y)
        Y_predictions = model(X)
        acc_score += torch.sum(torch.argmax(Y_predictions,dim=1) == Y).item()
        items_total += Y.shape[0] 

        loss = criterion(Y_predictions, Y)

        loss_score += loss.item() * Y.shape[0] 
    return (loss_score / items_total), (acc_score / items_total)

In [87]:
for epoch in range(5):
    loss_score = 0
    acc_score = 0
    items_total = 0
    nn_model.train()
    for i in range(0, Y_train.shape[0], BATCH_SIZE):
        X = X_train[i:i+BATCH_SIZE]
        X = torch.tensor(X.astype(np.float32).todense())
        Y = Y_train[i:i+BATCH_SIZE]

        Y = torch.tensor(Y)
        Y_predictions = nn_model(X)
        acc_score += torch.sum(torch.argmax(Y_predictions,dim=1) == Y).item()
        items_total += Y.shape[0] 

        optimizer.zero_grad()
        loss = criterion(Y_predictions, Y)
        loss.backward()
        optimizer.step()


        loss_score += loss.item() * Y.shape[0]

    
    display(epoch)
    display(get_loss_acc(nn_model, X_train, Y_train))
    display(get_loss_acc(nn_model, X_dev, Y_dev))

0

(1.3561987912015627, 0.7509723040659988)

(1.3750462425433523, 0.6861081654294804)

1

(1.172515784211909, 0.7780789628756629)

...

(0.9343988647444078, 0.8043606364172068)

(0.9874364811441173, 0.7408978437610463)

4

(0.8541374384970544, 0.8139068945197407)

(0.9145868947540504, 0.7490279250618593)

In [88]:
X.shape

torch.Size([5, 10000])

In [89]:
newsgroups_train_text

["From: DSHAL@vmd.cso.uiuc.edu\nSubject: Re: Clintons views on Jerusalem\nOrganization: C.C.S.O.\nLines: 10\n\nIt seems that President Clinton can recognize Jerusalem as Israels capitol\nwhile still keeping his diplomatic rear door open by stating that the Parties\nconcerned should decide the city's final status. Even as I endorse Clintons vie\nw (of course), it is definitely a matter to be decided upon by Israel (and\nother participating neighboring contries).\nI see no real conflict in stating both views, nor expect any better from\npoliticians.\n-----\nDavid Shalhevet / dshal@vmd.cso.uiuc.edu / University of Illinois\nDept Anim Sci / 220 PABL / 1201 W. Gregory Dr. / Urbana, IL 61801\n",
 'From: david@stat.com (David Dodell)\nSubject: HICN610 Medical News Part 4/4\nReply-To: david@stat.com (David Dodell)\nDistribution: world\nOrganization: Stat Gateway Service, WB7TPY\nLines: 577\n\n------------- cut here -----------------\nlimits of AZT\'s efficacy and now suggest using the drug  ei

### Podejście softmax z embeddingami na przykładzie NER

In [43]:
# !pip install torchtext
# !pip install datasets

https://www.aclweb.org/anthology/W03-0419.pdf

In [90]:
dataset = load_dataset("conll2003")

Reusing dataset conll2003 (/home/kuba/.cache/huggingface/datasets/conll2003/conll2003/1.0.0/63f4ebd1bcb7148b1644497336fd74643d4ce70123334431a3c053b7ee4e96ee)


  0%|          | 0/3 [00:00<?, ?it/s]

In [ ]:
Ala ma kota

Jacek ma 2 psy



<pad> Ala ma kota

Jacek ma 2 psy




In [91]:

import torchtext.vocab

def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    
    vocab = torchtext.vocab.vocab(counter, specials=['<unk>', '<pad>', '<bos>', '<eos>'])
    vocab.set_default_index(0)
    return vocab

In [92]:
vocab = build_vocab(dataset['train']['tokens'])

In [93]:
dataset['train']['tokens']

[['EU', 'rejects', 'German', 'call', 'to', 'boycott', 'British', 'lamb', '.'],
 ['Peter', 'Blackburn'],
 ['BRUSSELS', '1996-08-22'],
 ['The',
  'European',
  'Commission',
  'said',
  'on',
  'Thursday',
  'it',
  'disagreed',
  'with',
  'German',
  'advice',
  'to',
  'consumers',
  'to',
  'shun',
  'British',
  'lamb',
  'until',
  'scientists',
  'determine',
  'whether',
  'mad',
  'cow',
  'disease',
  'can',
  'be',
  'transmitted',
  'to',
  'sheep',
  '.'],
 ['Germany',
  "'s",
  'representative',
  'to',
  'the',
  'European',
  'Union',
  "'s",
  'veterinary',
  'committee',
  'Werner',
  'Zwingmann',
  'said',
  'on',
  'Wednesday',
  'consumers',
  'should',
  'buy',
  'sheepmeat',
  'from',
  'countries',
  'other',
  'than',
  'Britain',
  'until',
  'the',
  'scientific',
  'advice',
  'was',
  'clearer',
  '.'],
 ['"',
  'We',
  'do',
  "n't",
  'support',
  'any',
  'such',
  'recommendation',
  'because',
  'we',
  'do',
  "n't",
  'see',
  'any',
  'grounds',
  'fo

In [94]:
len(vocab.get_itos())

23627

In [95]:
vocab['on']

21

In [96]:
def data_process(dt):
    return [ torch.tensor([vocab['<bos>']] +[vocab[token]  for token in  document ] + [vocab['<eos>']], dtype = torch.long) for document in dt]


In [97]:
def labels_process(dt):
    return [ torch.tensor([0] + document + [0], dtype = torch.long) for document in dt]


In [98]:
train_tokens_ids = data_process(dataset['train']['tokens'])

In [99]:
test_tokens_ids = data_process(dataset['test']['tokens'])

In [100]:
train_labels = labels_process(dataset['train']['ner_tags'])

In [101]:
test_labels = labels_process(dataset['test']['ner_tags'])

In [105]:
dataset['train'][1]

{'id': '1',
 'tokens': ['Peter', 'Blackburn'],
 'pos_tags': [22, 22],
 'chunk_tags': [11, 12],
 'ner_tags': [1, 2]}

In [104]:
train_tokens_ids[1]

tensor([ 2, 13, 14,  3])

In [106]:
max([max(x) for x in dataset['train']['ner_tags'] if x])

8

In [110]:
class NERModel(torch.nn.Module):

    def __init__(self,):
        super(NERModel, self).__init__()
        self.emb = torch.nn.Embedding(23627,200)
        self.fc1 = torch.nn.Linear(600,9)
        #self.softmax = torch.nn.Softmax(dim=1)
        # nie trzeba, bo używamy https://pytorch.org/docs/stable/generated/torch.nn.CrossEntropyLoss.html
        # jako kryterium
        

    def forward(self, x):
        x = self.emb(x)
        x = x.reshape(600) 
        x = self.fc1(x)
        #x = self.softmax(x)
        return x

In [120]:
train_tokens_ids[10_000]

tensor([    2,  2036, 11867, 18826,   133,  7609,   135, 18827,     3])

In [119]:
train_tokens_ids[10_000][1:4]

tensor([ 2036, 11867, 18826])

In [121]:
ner_model = NERModel()

In [125]:
ner_model(train_tokens_ids[10_000][1:4])

tensor([-0.4334,  0.5433,  0.5576, -0.6093,  0.3312, -0.4221,  0.3375, -0.9720,
         0.4530], grad_fn=<AddBackward0>)

In [126]:
criterion = torch.nn.CrossEntropyLoss()

In [127]:
optimizer = torch.optim.Adam(ner_model.parameters())

In [128]:
len(train_labels)

14042

In [129]:
for epoch in range(2):
    loss_score = 0
    acc_score = 0
    prec_score = 0
    selected_items = 0
    recall_score = 0
    relevant_items = 0
    items_total = 0
    ner_model.train()
    #for i in range(len(train_labels)):
    for i in range(100):
        for j in range(1, len(train_labels[i]) - 1):
    
            X = train_tokens_ids[i][j-1: j+2]
            Y = train_labels[i][j: j+1]

            Y_predictions = ner_model(X)
            
            
            acc_score += int(torch.argmax(Y_predictions) == Y)
            
            if torch.argmax(Y_predictions) != 0:
                selected_items +=1
            if  torch.argmax(Y_predictions) != 0 and torch.argmax(Y_predictions) == Y.item():
                prec_score += 1
            
            if  Y.item() != 0:
                relevant_items +=1
            if  Y.item() != 0 and torch.argmax(Y_predictions) == Y.item():
                recall_score += 1
            
            items_total += 1

            
            optimizer.zero_grad()
            loss = criterion(Y_predictions.unsqueeze(0), Y)
            loss.backward()
            optimizer.step()


            loss_score += loss.item() 
    
    precision = prec_score / selected_items
    recall = recall_score / relevant_items
    f1_score = (2*precision * recall) / (precision + recall)
    display('epoch: ', epoch)
    display('loss: ', loss_score / items_total)
    display('acc: ', acc_score / items_total)
    display('prec: ', precision)
    display('recall: : ', recall)
    display('f1: ', f1_score)

'epoch: '

0

'loss: '

1.034957685828143

'acc: '

...

0.8061224489795918

'recall: : '

0.6528925619834711

'f1: '

0.7214611872146119

In [131]:
loss_score = 0
acc_score = 0
prec_score = 0
selected_items = 0
recall_score = 0
relevant_items = 0
items_total = 0
ner_model.eval()
for i in range(100):
#for i in range(len(test_labels)):
    for j in range(1, len(test_labels[i]) - 1):

        X = test_tokens_ids[i][j-1: j+2]
        Y = test_labels[i][j: j+1]

        try:
            Y_predictions = ner_model(X)
        except:
            import pdb; pdb.set_trace()

        acc_score += int(torch.argmax(Y_predictions) == Y)

        if torch.argmax(Y_predictions) != 0:
            selected_items +=1
        if  torch.argmax(Y_predictions) != 0 and torch.argmax(Y_predictions) == Y.item():
            prec_score += 1

        if  Y.item() != 0:
            relevant_items +=1
        if  Y.item() != 0 and torch.argmax(Y_predictions) == Y.item():
            recall_score += 1

        items_total += 1


        loss = criterion(Y_predictions.unsqueeze(0), Y)



        loss_score += loss.item() 

precision = prec_score / selected_items
recall = recall_score / relevant_items
f1_score = (2*precision * recall) / (precision + recall)
display('loss: ', loss_score / items_total)
display('acc: ', acc_score / items_total)
display('prec: ', precision)
display('recall: : ', recall)
display('f1: ', f1_score)

'loss: '

0.9228665271918766

'acc: '

0.7187060478199718

'prec: '

0.2782152230971129

'recall: : '

0.31547619047619047

'f1: '

0.29567642956764295

### Zadanie domowe

- nazwa: sequence labelling prosta siec ff
- stworzyć klasyfikator bazujący na sieci neuronowej feed forward w pytorchu (można bazować na tym jupyterze lub nie).
- klasyfikator powinien obejmować dodatkowe cechy (np. długość wyrazu, czy wyraz zaczyna się od wielkiej litery, stemmming słowa, czy zawiera cyfrę)
- stworzyć predykcje w plikach dev-0/out.tsv oraz test-A/out.tsv
- wynik fscore powinien wynosić conajmniej 0.60
- termin 08.06, 80 punktów
